## Using WMS Protocol

In this example the geojson library is used to help find the bounding box of a scene. Be sure to install this library.

> pip install geojson

In [ ]:
import geojson
import json
import requests

SEARCH_API_ENDPOINT = 'https://search.foundation.api.oneatlas.airbus.com/api/v2/opensearch'

access_token = input("Enter your access token")
scene_id = input("Enter the scene source identifier")
download_path = input("Path to download to")

headers = {
    "Authorization": f"Bearer {access_token}"
}
body = {
    "sourceIdentifier": scene_id
}
response = requests.post(f"{SEARCH_API_ENDPOINT}", json=body, headers=headers)
response.raise_for_status()

body = response.json()
wms_link = body['features'][0]['_links']['wms']['href']

The geojson library is used to load the geometry so it is easier to get to the coordinate pairs. Once available, the bounding box can be figured out from the coordinate list.

In [ ]:
geometry = geojson.base.GeoJSON.to_instance(body['features'][0]['geometry'])
min_x = min([x for x,y in list(geojson.utils.coords(geometry))])
max_x = max([x for x,y in list(geojson.utils.coords(geometry))])
min_y = min([y for x,y in list(geojson.utils.coords(geometry))])
max_y = max([y for x,y in list(geojson.utils.coords(geometry))])
bbox = f"{min_y},{min_x},{max_y},{max_x}"
print(f"Bounding box is {bbox}")

Now form a request to get an image from the WMS service using the computed bounding box.

In [ ]:
params = {
    'REQUEST': 'GetMap',
    'VERSION': '1.3.0',
    'LAYERS': 'layer_0',
    'CRS': 'EPSG:4326',
    'BBOX': bbox,
    'WIDTH': 600,
    'HEIGHT': 400,
    'FORMAT': 'image/png'
}
with requests.get(wms_link, params=params, headers=headers, stream=True) as r:
        r.raise_for_status()
        with open(download_path, 'wb') as f:
            for chunk in r.iter_content(chunk_size=8192): 
                f.write(chunk)
      
print(f"Downloaded to {download_path}")